Creating tables in SQL
---------------------

Before we actually get into basic SQL queries (**asking questions _of_ data in tables**), we'll look at some of the basics about how to **create** tables.

In [ ]:
%load_ext sql
%sql sqlite://

We will start by creating a SQL database on Books and Authors. Let's first create a table named `Author` with three attributes:
> * `authorid`
> * `firstname`
> * `lastname`

In [ ]:
%%sql
CREATE TABLE Author(
    authorid INTEGER PRIMARY KEY,    
    firstname CHAR(20),
    lastname CHAR(30)
);


Let's see how to view the **schema** of existing tables. There are several ways, including but not limited to:
* DESCRIBE tablename
* SHOW CREATE TABLE tablename
* SHOW COLUMNS tablename

Unfortunately, support for these varies widely between DBMSs, and is also limited by our IPython interface (for example sqlite, which we are using, does not support the above; it does have a `.schema tablename` command, however this doesn't work in IPython notebooks...)

One that does work for us here though is:

In [ ]:
#Metadata in SQLite can be obtained using the PRAGMA command
%sql PRAGMA table_info(Author);

And, we can get the exact statement used to create the table as follows:

In [ ]:
%sql SELECT sql FROM sqlite_master WHERE name = 'Author';

To insert a new tuple in a table, we use the SQL command INSERT.

In [ ]:
%sql INSERT INTO Author VALUES('001', 'Dan', 'Brown');

Alternatively, we can also insert a tuple by specifying the corresponding attributes.

In [ ]:
%sql INSERT INTO Author(authorid, lastname, firstname) VALUES('002', 'Clarke', 'Arthur');

To check that the tuples has indeed been added to the table, we can ask:

In [ ]:
%sql SELECT * FROM Author;

The attribute `authorid` is a *primary key*. This means that it is not possible to add in the table another author with the same value. For example, see what happens when we attempt to violate the constraint.

In [ ]:
%sql INSERT INTO Author VALUES('001', 'Jules', 'Verne');

Foreign Keys
------------------

To make SQLite enforce foreign key constraints, we need to run the following command

In [ ]:
%sql PRAGMA foreign_keys = ON;

In [ ]:
%%sql
CREATE TABLE Book(
  bookid INTEGER PRIMARY KEY,
  title TEXT,
  authorid INTEGER,
  FOREIGN KEY (authorid) REFERENCES Author(authorid)
);

In [ ]:
%sql INSERT INTO Book VALUES(5634, 'Da Vinvi Code', 001);

If however we try to insert a tuple that has an `authorid` not in the table `Author`, then it fails.

In [ ]:
%sql INSERT INTO Book VALUES(5674, 'Enders Game', 003);

The same problem will occur if we try to delete from `Author` a tuple that is referred to from the table `Book`.

In [ ]:
%sql DELETE FROM Author WHERE authorid = 1 ;

Or if we try to update the value of the tuple.

In [ ]:
%%sql
UPDATE Author
SET authorid = 4
WHERE authorid = 1 ;

The *default* behavior of SQL is to reject actions (insertions, deletions, updates) that violate the foreign key constraints. We can change this behavior by changing the table definition.

In [ ]:
%%sql
DROP Table Book;
CREATE TABLE Book(
  bookid INTEGER PRIMARY KEY,
  title TEXT,
  authorid INTEGER,
  FOREIGN KEY (authorid) REFERENCES Author(authorid)
    ON UPDATE CASCADE
    ON DELETE CASCADE
);

INSERT INTO Book VALUES(5634, 'Da Vinvi Code', 001);

Now let's try again!

In [ ]:
%%sql 
UPDATE Author
SET authorid = 4
WHERE authorid = 1 ;